In [1]:
import os
import pandas as pd
import numpy as np

import json

#libraries for data visualization
import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.pylab as pylab
%matplotlib inline
import seaborn as sns
sns.set_color_codes("pastel")

#map 
import folium
from folium import plugins

In [2]:
filepath = "/Users/reejungkim/Documents/Git/Production analysis/Online Retail.xlsx"
df = pd.read_excel(filepath, sheet_name = 'Online Retail')
df.head()

InvoiceNo StockCode                          Description  Quantity  \
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

          InvoiceDate  UnitPrice  CustomerID         Country  
0 2010-12-01 08:26:00       2.55     17850.0  United Kingdom  
1 2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
2 2010-12-01 08:26:00       2.75     17850.0  United Kingdom  
3 2010-12-01 08:26:00       3.39     17850.0  United Kingdom  
4 2010-12-01 08:26:00       3.39     17850.0  United Kingdom

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 541909 entries, 0 to 541908
Data columns (total 8 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   InvoiceNo    541909 non-null  object        
 1   StockCode    541909 non-null  object        
 2   Description  540455 non-null  object        
 3   Quantity     541909 non-null  int64         
 4   InvoiceDate  541909 non-null  datetime64[ns]
 5   UnitPrice    541909 non-null  float64       
 6   CustomerID   406829 non-null  float64       
 7   Country      541909 non-null  object        
dtypes: datetime64[ns](1), float64(2), int64(1), object(4)
memory usage: 33.1+ MB


In [4]:
df.CustomerID = df.CustomerID.astype(str)

In [5]:
df['TotalPurchase'] = df.Quantity * df.UnitPrice

In [6]:
df['year-m'] = df['InvoiceDate'].dt.strftime('%Y-%m') #df['InvoiceDate'].apply(lambda x: x.strftime("%Y-%m"))
df.sort_values(by='InvoiceDate', ascending=True, inplace=True)

### load local json file

In [7]:
#json_file_path = r"./Users/reejungkim/Documents/geo_countries.json"
rfile = open("/Users/reejungkim/Documents/Git/geo_countries.json", "r", encoding='utf-8').read() 
jsonData = json.loads(rfile)

In [8]:
geo_json_data = pd.read_json("/Users/reejungkim/Documents/Git/geo_countries.json")
geo_json_data.head()

geo_json_data.features

geo_df = pd.json_normalize(geo_json_data.features)
geo_df.head()

type  properties.scalerank properties.featurecla  properties.labelrank  \
0  Feature                     1       Admin-0 country                     4   
1  Feature                     1       Admin-0 country                     6   
2  Feature                     1       Admin-0 country                     2   
3  Feature                     1       Admin-0 country                     5   
4  Feature                     1       Admin-0 country                     3   

  properties.sovereignt properties.sov_a3  properties.adm0_dif  \
0           The Bahamas               BHS                    0   
1                Belize               BLZ                    0   
2                Canada               CAN                    0   
3            Costa Rica               CRI                    0   
4                  Cuba               CUB                    0   

   properties.level    properties.type properties.admin  ...  \
0                 2  Sovereign country      The Bahamas  ...   
1                 2  Sovereign country           Belize  ...   
2                 2  Sovereign country           Canada  ...   
3                 2  Sovereign country       Costa Rica  ...   
4                 2  Sovereign country             Cuba  ...   

  properties.subregion       properties.region_wb properties.name_len  \
0            Caribbean  Latin America & Caribbean                   7   
1      Central America  Latin America & Caribbean                   6   
2     Northern America              North America                   6   
3      Central America  Latin America & Caribbean                  10   
4            Caribbean  Latin America & Caribbean                   4   

  properties.long_len  properties.abbrev_len properties.tiny  \
0                   7                      4             -99   
1                   6                      6             -99   
2                   6                      4             -99   
3                  10                      4             -99   
4                   4                      4             -99   

  properties.homepart  properties.filename geometry.type  \
0                   1          BHS.geojson  MultiPolygon   
1                   1          BLZ.geojson       Polygon   
2                   1          CAN.geojson  MultiPolygon   
3                   1          CRI.geojson       Polygon   
4                   1          CUB.geojson       Polygon   

                                geometry.coordinates  
0  [[[[-77.53466, 23.75975], [-77.78, 23.71], [-7...  
1  [[[-89.14308041050332, 17.80831899664932], [-8...  
2  [[[[-63.6645, 46.55001], [-62.9393, 46.41587],...  
3  [[[-82.96578304719736, 8.225027980985985], [-8...  
4  [[[-82.26815121125706, 23.188610744717703], [-...  

[5 rows x 67 columns]

### or load json file from git

In [9]:
import requests
url = 'https://raw.githubusercontent.com/reejungkim/User-Analysis/master/geo_countries.json'
jsonData = json.loads(requests.get(url).text)

# Map

In [10]:
geo_map = folium.Map(location=[37, -102], zoom_start=2) #, tiles='Stamen Toner') tiles='Stamen Terrain') tiles='cartodbpositron')
geo_map

## Add json data to the map

In [11]:
folium.GeoJson(jsonData, name='json_data').add_to(geo_map)
geo_map

## Reflect quantity ordered on the map

In [12]:
df_sales = df.groupby('Country').agg({'CustomerID': lambda customer: customer.count(),
                                        'Quantity': lambda quant: quant.sum(),
                                        'TotalPurchase': lambda price: price.sum()}).reset_index()
df_sales['AvgPurchasePerCustomer'] = df_sales.TotalPurchase/df_sales.CustomerID

In [13]:
df_sales.head()

Country  CustomerID  Quantity  TotalPurchase  AvgPurchasePerCustomer
0  Australia        1259     83653      137077.27              108.877895
1    Austria         401      4827       10154.32               25.322494
2    Bahrain          19       260         548.40               28.863158
3    Belgium        2069     23152       40910.96               19.773301
4     Brazil          32       356        1143.60               35.737500

In [14]:
geo_map = folium.Map(location=[54.7023545, -3.2765753], zoom_start=2) #, tiles='Stamen Toner') tiles='Stamen Terrain') tiles='cartodbpositron')
#[54.7023545, -3.2765753] <- U.K.

folium.Choropleth(
    geo_data= jsonData,
    name= 'choropleth',
    data= df_sales,
    columns=['Country', 'AvgPurchasePerCustomer', 'CustomerID'],
    key_on='properties.sovereignt',
    fill_color= 'OrRd',
    fill_opacity=0.8,
    line_opacity=0.2,
    legend_name='Average puchase per customer',
    highlight=True,
    line_color='blue', 
    reset= True
).add_to(geo_map)

folium.LayerControl(collapsed=True).add_to(geo_map)
geo_map

## Visualization of sales

In [15]:
geo_map = folium.Map(location=[54.7023545, -3.2765753], zoom_start=2) #, tiles='Stamen Toner') tiles='Stamen Terrain') tiles='cartodbpositron')

choropleth = folium.Choropleth(
    geo_data= jsonData,
    name= 'choropleth',
    data= df_sales,
    columns=['Country', 'TotalPurchase', 'CustomerID'],
    key_on='properties.sovereignt',
    fill_color= 'YlGn', #'BuGn', 'BuPu', 'GnBu', 'OrRd', 'PuBu', 'PuBuGn', 'PuRd',
    fill_opacity=0.5,
    line_opacity=0.2,
    legend_name='Total purchase',
    highlight=True,
    line_color='blue', 
    reset= True
).add_to(geo_map)

folium.LayerControl(collapsed=True).add_to(geo_map)
geo_map

## Visualization of sales by quantile

In [16]:
df_sales['TotalPurchase'].quantile([0, 0.25, 0.5, 0.75, 1])

0.00    1.311700e+02
0.25    2.053077e+03
0.50    1.013568e+04
0.75    3.628209e+04
1.00    8.187806e+06
Name: TotalPurchase, dtype: float64

df_sales.TotalPurchase.astype('float')

In [52]:
geo_map = folium.Map(location=[54.7023545, -3.2765753], zoom_start=2) #, tiles='Stamen Toner') tiles='Stamen Terrain') tiles='cartodbpositron')

bin_scale = df_sales['TotalPurchase'].quantile([0, 0.25, 0.5, 0.75, 0.9, 0.99, 1]).tolist()

choropleth = folium.Choropleth(
    geo_data= jsonData,
    name= 'choropleth',
    data= df_sales,
    columns=['Country','TotalPurchase'],
    key_on='properties.sovereignt',
    fill_color= 'YlGn', #'BuGn', 'BuPu', 'GnBu', 'OrRd', 'PuBu', 'PuBuGn', 'PuRd',
    fill_opacity=0.5,
    line_opacity=0.2,
    legend_name='total purchase',
    bins= bin_scale,
    highlight=True,
    line_color='blue',
    reset= True
).add_to(geo_map)

geo_map

## Add a mark to a country with highest sales value

In [18]:
#library for getting longitudate and latitude info
#get longitude and latitude of the country
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent='n/a')

city ="London"
country ="Uk"
loc = geolocator.geocode(city+','+ country)

print("latitude is :-" ,loc.latitude,"\nlongtitude is:-" ,loc.longitude)

In [53]:
#country with higest sales
country_highest_sales = df_sales.sort_values(by='TotalPurchase', ascending=False)[:1]
country_highest_sales['Country'].values
print("Country with highest sales value : ",country_highest_sales['Country'].values)

location_highest_sales = geolocator.geocode(country_highest_sales['Country'].values)
location_highest_sales = location_highest_sales.latitude, location_highest_sales.longitude
print("longitude & latidue: ", location_highest_sales)

Country with highest sales value :  ['United Kingdom']
longitude & latidue:  (54.7023545, -3.2765753)


In [54]:
#country with higest average sales per customer
country_highest_avg_sales = df_sales.sort_values(by='AvgPurchasePerCustomer', ascending=False)[:1]['Country']
country_highest_avg_sales.values
print("Country with highest average sales value : ",country_highest_avg_sales.values)

location_avg_sales = geolocator.geocode(country_highest_avg_sales.values)
location_avg_sales = location_avg_sales.latitude, location_avg_sales.longitude
print("longitude & latidue: ", location_avg_sales)

Country with highest average sales value :  ['Netherlands']
longitude & latidue:  (52.5001698, 5.7480821)


In [56]:
folium.LayerControl(collapsed=True).add_to(geo_map)

#Add marker pointing London to the map
text = str(country_highest_sales['Country'].values) + " " + str(country_highest_sales['TotalPurchase'].values)
folium.Marker(location_highest_sales, popup= text, 
             icon = folium.Icon(color='red', icon='info-sign')).add_to(geo_map)

#Add circle marker to the map
folium.CircleMarker(location_avg_sales, 
                    radius=10, 
                    color='#3186cc', 
                    fill_color='#3186cc',
                   popup='Highest average sales per customer').add_to(geo_map)

geo_map

## save to html file

In [22]:
geo_map.save('PurchaseByCountry.html')